# 🏠🏠🏠 Projet Kaggle : Régression : Suite de la Modélisation GLM 🏠🏠🏠

## Initialisation

### Importation des bibliothèques nécessaires


In [1]:
import json

import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
import statsmodels.api as sm
import statsmodels.formula.api as smf
from sklearn.base import BaseEstimator, RegressorMixin
from sklearn.metrics import (
    make_scorer,
    max_error,
    mean_absolute_error,
    median_absolute_error,
    r2_score,
    root_mean_squared_error,
)
from sklearn.model_selection import cross_validate, train_test_split

### Importation des données


In [2]:
with open("../data/processed/dtype_dict.json") as f:
    dtype_dict = json.load(f)

train = pd.read_csv(
    "../data/processed/train.csv",
    delimiter=",",
    encoding="utf-8",
    index_col="Id",
    dtype=dtype_dict,
)

test = pd.read_csv(
    "../data/processed/test.csv",
    delimiter=",",
    encoding="utf-8",
    index_col="Id",
    dtype=dtype_dict,
)

dfs = [train, test]

### Reprise des transformations interessantes


In [3]:
neighborhoods_to_keep = [
    "Brookside",
    "Clear Creek",
    "Crawford",
    "Northridge",
    "Northridge Heights",
    "Stone Brook",
    "Veenker",
]

for df in dfs:
    df["Neighborhood_agg2"] = np.where(
        df["Neighborhood"].isin(neighborhoods_to_keep), df["Neighborhood"], "Autre"
    )
    df.rename(
        columns={"1stFlrSF": "FirstFlrSF", "2ndFlrSF": "SecondFlrSF"}, inplace=True
    )
    df["FullBath_tot"] = df["FullBath"] + df["BsmtFullBath"]
    df["HalfBath_tot"] = df["HalfBath"] + df["BsmtHalfBath"]

### Découpage de SecondFlrSF


In [4]:
# Appliquer pd.qcut sur l'ensemble d'entraînement pour obtenir les bornes
_, bins = pd.qcut(train["SecondFlrSF"], q=15, duplicates="drop", retbins=True)

# Remplacer la borne supérieure du dernier intervalle par l'infini
bins[-1] = np.inf

In [5]:
for df in dfs:
    df["SecondFlrSF_cut"] = pd.cut(df["SecondFlrSF"], bins=bins, include_lowest=True)

### Séparation en train test


In [6]:
df_train, df_test = train_test_split(
    train,
    test_size=0.33,
    random_state=42,
)

## Reprise de la dernière régression avec le decoupage de SecondFlrSF

### Création de la formule


In [ ]:
selection = [
    "TotalBsmtSF",
    "FirstFlrSF",
    # "SecondFlrSF",
    "SecondFlrSF_cut",
    "GarageArea",
    "LotFrontage",
    "LotArea",
    "HalfBath_tot",
    "FullBath_tot",
    "LotConfig_agg",
    "GarageQual_agg",
    "Fireplaces_optb",
    "KitchenQual",
    "BsmtExposure_ord",
    "BsmtQual",
    "ExterQual",
    "Exterior1st_agg",
    "OverallQual_ord",
    "Neighborhood_agg2",
    "MSZoning",
    "BsmtFinType1_ord",
    "CentralAir",
    "HouseAgeAtSale",
]

debut_formule = "SalePrice ~"

debut_cat = " + C("

fin_cat = ")"

formule = debut_formule

for col in selection:
    if pd.api.types.is_any_real_numeric_dtype(df_train[col]) or col.endswith("_ord"):
        formule = str(formule) + " + " + str(col)
    else:
        formule = str(formule) + debut_cat + str(col) + fin_cat

### Définition du modèle


In [8]:
reg1 = smf.glm(
    formula=formule,
    data=df_train,
    family=sm.families.Gamma(link=sm.families.links.Identity()),
)

c:\Users\guill\miniconda3\envs\house-prices-env\Lib\site-packages\statsmodels\genmod\generalized_linear_model.py:308: DomainWarning: The Identity link function does not respect the domain of the Gamma family.
  warnings.warn((f"The {type(family.link).__name__} link function "


### Entrainement du modèle


In [9]:
res1 = reg1.fit()

### Analyse globale


In [10]:
print(res1.summary())

                 Generalized Linear Model Regression Results                  
Dep. Variable:              SalePrice   No. Observations:                  978
Model:                            GLM   Df Residuals:                      925
Model Family:                   Gamma   Df Model:                           52
Link Function:               Identity   Scale:                        0.016758
Method:                          IRLS   Log-Likelihood:                -11166.
Date:                Mon, 24 Feb 2025   Deviance:                       16.809
Time:                        09:01:54   Pearson chi2:                     15.5
No. Iterations:                    19   Pseudo R-squ. (CS):             0.9998
Covariance Type:            nonrobust                                         
                                                                        coef    std err          z      P>|z|      [0.025      0.975]
----------------------------------------------------------------------------

### Critère AIC


In [11]:
res1.aic

22437.80067561067

### Critère BIC


In [12]:
res1.bic_llf

22696.732688122516

## Analyses des performances

#### Définition des différents thèmes pour les figures plotly


In [13]:
# Template personnalisé
monTheme = go.layout.Template(
    layout=dict(
        template="simple_white",
        autosize=True,
        font=dict(family="Arial", size=15, color="#000000"),
        title=dict(font=dict(size=35, family="Arial"), x=0.5),
        xaxis=dict(tickangle=-35, automargin=True),
        yaxis=dict(tickangle=-35, automargin=True),
    )
)

# Enregistrement du template
pio.templates["monTheme"] = monTheme

# Définition du template comme template par défaut
pio.templates.default = "monTheme"

# Même principe, style de boutons par defaut
# Ne peut pas rentrer dans les templates
styleBoutons = dict(
    bgcolor="#6B6B6B",
    bordercolor="#000000",
    borderwidth=1.5,
    direction="right",
    font_weight=700,
    showactive=True,
    type="buttons",
    x=1,
    xanchor="right",
    y=1.2,
    yanchor="top",
)

mesPolices = {
    "font-size": 25,
    "font-family": "Arial",
    "font-weight": 700,
    "color": "Black",
}

rouge = "rgb(200, 10, 10)"

res = "Résidus"

## Analyses des performances

### Calculs des prédictions


In [14]:
df_test["SalePrice_pred"] = res1.predict(df_test[selection])

In [15]:
df_test[["SalePrice_pred", "SalePrice"]].head(10)

SalePrice_pred  SalePrice
Id                             
893    136039.689630     154500
1106   360871.970939     325000
414    108957.411154     115000
523    162578.699112     159000
1037   315496.391705     315500
615     75692.811183      75500
219    226960.425717     311500
1161   157961.513360     146000
650     79638.521767      84500
888    133290.117154     135500

### Quelques métriques bien connues


In [ ]:
def plot_perf(y_true: np.ndarray, y_pred: np.ndarray) -> pd.DataFrame:
    return pd.DataFrame(
        {
            "MAE": [mean_absolute_error(y_true, y_pred)],
            "RMSE": [root_mean_squared_error(y_true, y_pred)],
            "MEE": [median_absolute_error(y_true, y_pred)],
            "ME": [max_error(y_true, y_pred)],
            "R2": [r2_score(y_true, y_pred)],
        }
    )

In [17]:
plot_perf(df_test["SalePrice"], df_test["SalePrice_pred"])

MAE          RMSE           MEE             ME        R2
0  18210.474424  32030.809791  11621.387597  280495.108583  0.860248

#### Forme des résidus


In [18]:
df_test["residus"] = df_test["SalePrice"] - df_test["SalePrice_pred"]

In [19]:
def residuals_density(df: pd.DataFrame, res_col: str):
    residuals_density = px.histogram(
        df, x=res_col, marginal="box", color_discrete_sequence=[rouge]
    )

    residuals_density.update_layout(
        title_text="Répartition des résidus",
        xaxis_title=res,
        yaxis_title="Nombre",
        showlegend=False,
    )

    residuals_density.show()

In [20]:
residuals_density(df_test, "residus")

#### Résidus en fonction du Prix de vente


In [ ]:
def scat_res_price(df: pd.DataFrame, res_col: str, target_col: str):
    scat_res_price = px.scatter(
        df,
        x=target_col,
        y=res_col,
        color_discrete_sequence=[rouge],
    )

    scat_res_price.update_layout(
        title_text="Résidus (valeur réelle - valeur prédite) en fonction du Prix des maisons",
        xaxis_title="Prix de vente",
        yaxis_title=res,
    )

    scat_res_price.show()

In [ ]:
scat_res_price(
    df_test,
    "residus",
    "SalePrice",
)

#### Résidus en fonction des variables quantitatives


In [ ]:
def scat(df, first_col: str, res_col: str, numerical_cols: list):
    # Définition de la figure type nuages de points
    scat = go.Figure(
        go.Scatter(
            x=df[first_col],
            y=df_test[res_col],
            mode="markers",
            marker_color=rouge,
        )
    )

    boutons_x = [
        dict(
            label=f"x - {x}",
            method="update",
            args=[
                {"x": [df[x]]},
                {"xaxis": {"title": x}},
            ],
        )
        for x in numerical_cols
    ]

    # Mise à jour du layout
    scat.update_layout(
        title_text="Relation entre les résidus et la variable quantitative séléctionnée",
        xaxis_title=first_col,
        yaxis_title=res,
        updatemenus=[
            dict(
                buttons=boutons_x,
                direction="up",  # Set to 'down' or 'up' for dropdown
                showactive=True,
                x=1,
                xanchor="right",
                y=-0.25,
                yanchor="bottom",  # Custom styles specified here
                bgcolor=styleBoutons["bgcolor"],
                bordercolor=styleBoutons["bordercolor"],
                borderwidth=styleBoutons["borderwidth"],
            ),
        ],
    )

    # Affichage de la figure
    scat.show()

In [ ]:
numerical_cols = [
    col
    for col in df_test.columns
    if pd.api.types.is_any_real_numeric_dtype(df_test[col])
]

scat(
    df_test,
    "LotFrontage",
    "residus",
    numerical_cols,
)

#### Résidus en fonction des variables qualitatives sélectionnées


In [ ]:
def violin(df, first_col: str, res_col: str, categorical_cols: list):
    violin = go.Figure(
        go.Violin(
            x=df[first_col],
            y=df[res_col],
            fillcolor=rouge,
            line_color="black",
            marker_color="black",
            box_visible=True,
            meanline_visible=True,
        )
    )

    boutons_y = [
        dict(
            label=f"x - {x}",
            method="update",
            args=[
                {"x": [df[x]]},
                {"xaxis": {"title": x}},
            ],
        )
        for x in categorical_cols
    ]

    # Mise à jour du layout
    violin.update_layout(
        title_text="Relation entre les résidus et la variable qualitative sélectionnée",
        xaxis_title=first_col,
        yaxis_title=res,
        updatemenus=[
            dict(
                buttons=boutons_y,
                direction="up",  # Set to 'down' or 'up' for dropdown
                showactive=True,
                x=1,
                xanchor="right",
                y=-0.25,
                yanchor="bottom",  # Custom styles specified here
                bgcolor=styleBoutons["bgcolor"],
                bordercolor=styleBoutons["bordercolor"],
                borderwidth=styleBoutons["borderwidth"],
            ),
        ],
    )

    # Affichage de la figure
    violin.show()

In [ ]:
categorical_cols = [col for col in df_test.columns if df_test[col].dtype == "object"]

violin(df_test, "MSSubClass", "residus", categorical_cols)

Le changement en intervalles pour SecondFlrSF ne change pas vraiment le comportement du modèle. Je vais tout de même essayer sur les autres variables quantitatives avant de passer au stacking

## Reprise de la dernière régression avec le decoupage de SecondFlrSF

### Découpage des variables quantitatives


In [27]:
for col in [
    "TotalBsmtSF",
    "FirstFlrSF",
    "GarageArea",
    "LotFrontage",
    "LotArea",
    "HouseAgeAtSale",
]:
    _, bins = pd.qcut(train[col], q=15, duplicates="drop", retbins=True)

    bins[-1] = np.inf

    for df in [train, test, df_train, df_test]:
        col_name = col + "_cut"

        df[col_name] = pd.cut(df[col], bins=bins, include_lowest=True)

### Création de la formule


In [ ]:
selection = [
    "TotalBsmtSF_cut",
    "FirstFlrSF_cut",
    "SecondFlrSF_cut",
    "GarageArea_cut",
    "LotFrontage_cut",
    "LotArea_cut",
    "HalfBath_tot",
    "FullBath_tot",
    "LotConfig_agg",
    "GarageQual_agg",
    "Fireplaces_optb",
    "KitchenQual",
    "BsmtExposure_ord",
    "BsmtQual",
    "ExterQual",
    "Exterior1st_agg",
    "OverallQual_ord",
    "Neighborhood_agg2",
    "MSZoning",
    "BsmtFinType1_ord",
    "CentralAir",
    "HouseAgeAtSale_cut",
]


formule = debut_formule

for col in selection:
    if pd.api.types.is_any_real_numeric_dtype(df_train[col]) or col.endswith("_ord"):
        formule = str(formule) + " + " + str(col)
    else:
        formule = str(formule) + debut_cat + str(col) + fin_cat

### Définition du modèle


In [29]:
reg2 = smf.glm(
    formula=formule,
    data=df_train,
    family=sm.families.Gamma(link=sm.families.links.Identity()),
)

c:\Users\guill\miniconda3\envs\house-prices-env\Lib\site-packages\statsmodels\genmod\generalized_linear_model.py:308: DomainWarning:

The Identity link function does not respect the domain of the Gamma family.



### Entrainement du modèle


In [30]:
res2 = reg2.fit()

### Analyse globale


In [31]:
print(res2.summary())

                 Generalized Linear Model Regression Results                  
Dep. Variable:              SalePrice   No. Observations:                  978
Model:                            GLM   Df Residuals:                      850
Model Family:                   Gamma   Df Model:                          127
Link Function:               Identity   Scale:                        0.016361
Method:                          IRLS   Log-Likelihood:                -11102.
Date:                Mon, 24 Feb 2025   Deviance:                       14.715
Time:                        09:02:03   Pearson chi2:                     13.9
No. Iterations:                    27   Pseudo R-squ. (CS):             0.9998
Covariance Type:            nonrobust                                         
                                                                        coef    std err          z      P>|z|      [0.025      0.975]
----------------------------------------------------------------------------

## Analyses des performances

### Calculs des prédictions


In [32]:
df_test["SalePrice_pred"] = res2.predict(df_test[selection])

### Quelques métriques bien connues


In [33]:
plot_perf(df_test["SalePrice"], df_test["SalePrice_pred"])

MAE          RMSE           MEE             ME        R2
0  18234.798243  31899.906576  11796.179134  295113.897078  0.861388

### Analyses des résidus


In [34]:
df_test["residus"] = df_test["SalePrice"] - df_test["SalePrice_pred"]

In [35]:
residuals_density(df_test, "residus")

In [ ]:
scat_res_price(
    df_test,
    "residus",
    "SalePrice",
)

In [ ]:
scat(
    df_test,
    "LotFrontage",
    "residus",
    numerical_cols,
)

In [ ]:
violin(
    df_test,
    "MSSubClass",
    "residus",
    categorical_cols,
)

Le comportement n'est pas amelioré. Juste avant de passer à la méthode stacking, je vais essayer une validation croisée.

## Reprise du modèle et validation croisée


In [ ]:
selection = [
    "TotalBsmtSF",
    "FirstFlrSF",
    "SecondFlrSF",
    # "SecondFlrSF_cut",
    "GarageArea",
    "LotFrontage",
    "LotArea",
    "HalfBath_tot",
    "FullBath_tot",
    "LotConfig_agg",
    "GarageQual_agg",
    "Fireplaces_optb",
    "KitchenQual",
    "BsmtExposure_ord",
    "BsmtQual",
    "ExterQual",
    "Exterior1st_agg",
    "OverallQual_ord",
    "Neighborhood_agg2",
    "MSZoning",
    "BsmtFinType1_ord",
    "CentralAir",
    "HouseAgeAtSale",
]

formule = debut_formule

for col in selection:
    if pd.api.types.is_any_real_numeric_dtype(df_train[col]) or col.endswith("_ord"):
        formule = str(formule) + " + " + str(col)
    else:
        formule = str(formule) + debut_cat + str(col) + fin_cat

In [40]:
class GLMWrapper(BaseEstimator, RegressorMixin):
    """Wrapper pour utiliser un modèle GLM spécifique de statsmodels avec scikit-learn."""

    def __init__(self, formula, family):
        self.formula = formula
        self.family = family
        self.model = None

    def fit(self, X, y):
        # Combiner X et y dans un DataFrame pour utiliser la formule
        data = X.copy()
        data["SalePrice"] = y
        self.model = smf.glm(formula=self.formula, data=data, family=self.family).fit()
        return self

    def predict(self, X):
        # Prédire en utilisant le modèle ajusté
        data = X.copy()
        return self.model.predict(data)

In [41]:
# Créer le modèle GLM
glm_model = GLMWrapper(
    formula=formule, family=sm.families.Gamma(link=sm.families.links.Identity())
)

In [42]:
# Définir les métriques de performance
scoring = {
    "MAE": make_scorer(mean_absolute_error),
    "RMSE": make_scorer(root_mean_squared_error, greater_is_better=False),
    "MEE": make_scorer(median_absolute_error),
    "ME": make_scorer(max_error, greater_is_better=False),
    "R2": make_scorer(r2_score),
}

In [55]:
# Évaluer le modèle avec cross_validate
cv_results = pd.DataFrame(
    cross_validate(
        glm_model,
        X=train.drop(columns="SalePrice", axis=1),
        y=train["SalePrice"],
        cv=10,
        scoring=scoring,
        return_train_score=True,
        return_estimator=True,
        n_jobs=-1,
    )
)

In [56]:
cv_results

fit_time  score_time                                          estimator  \
0  0.500145    0.110862  GLMWrapper(family=<statsmodels.genmod.families...   
1  0.403925    0.062051  GLMWrapper(family=<statsmodels.genmod.families...   
2  0.408975    0.091157  GLMWrapper(family=<statsmodels.genmod.families...   
3  0.451557    0.093407  GLMWrapper(family=<statsmodels.genmod.families...   
4  0.420027    0.122592  GLMWrapper(family=<statsmodels.genmod.families...   
5  0.284978    0.058709  GLMWrapper(family=<statsmodels.genmod.families...   
6  0.398026    0.090013  GLMWrapper(family=<statsmodels.genmod.families...   
7  0.407195    0.087172  GLMWrapper(family=<statsmodels.genmod.families...   
8  0.414183    0.071585  GLMWrapper(family=<statsmodels.genmod.families...   
9  0.230754    0.055069  GLMWrapper(family=<statsmodels.genmod.families...   

       test_MAE     train_MAE     test_RMSE    train_RMSE      test_MEE  \
0  16223.285477  17785.787240 -21987.094534 -31829.866657  12102.633657   
1  17588.574201  17664.903806 -27010.237555 -31645.092019  11490.228750   
2  18139.482741  17687.318551 -26659.839821 -31892.133199  11445.084633   
3  21102.067655  17281.294153 -39373.377210 -30092.353924  12430.982075   
4  21805.974105  17232.882776 -36702.598937 -30630.285553  12421.151262   
5  15715.084610  17914.970318 -26913.543608 -31516.222046   9993.325953   
6  16512.282701  17739.276047 -25622.694357 -31639.773458  13292.201584   
7  16300.864402  17761.697149 -25064.247582 -31866.483745  12234.196415   
8  22325.554647  17071.895002 -53911.673860 -27658.243514  13569.751412   
9  16668.310928  17790.740504 -23445.931387 -31958.570726  13125.291844   

      train_MEE        test_ME       train_ME   test_R2  train_R2  
0  11380.996793  -67698.755945 -491957.961070  0.895785  0.843821  
1  11624.575251 -175355.668865 -491828.725690  0.884604  0.840973  
2  11678.546843 -117733.990403 -502679.508696  0.886816  0.838792  
3  11727.445530 -333534.984118 -500586.206359  0.774072  0.854986  
4  11490.495023 -240189.586704 -489948.784333  0.854458  0.842994  
5  11976.366883 -183613.672299 -486508.312474  0.877118  0.843631  
6  11326.514493 -203252.280698 -495358.265862  0.872347  0.844291  
7  11745.182572 -168081.553907 -505128.247691  0.874066  0.842440  
8  11209.358280 -506447.469864 -332030.813711  0.640536  0.874623  
9  11472.075315 -122017.157852 -495791.699132  0.895065  0.840962

In [59]:
# Identifier le modèle avec le meilleur score (par exemple, le meilleur R2)
best_model_index = np.argmax(cv_results["test_RMSE"])
best_model = cv_results["estimator"][best_model_index].model

In [60]:
best_model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                 Generalized Linear Model Regression Results                  
==============================================================================
Dep. Variable:              SalePrice   No. Observations:                 1314
Model:                            GLM   Df Residuals:                     1266
Model Family:                   Gamma   Df Model:                           47
Link Function:               Identity   Scale:                        0.016614
Method:                          IRLS   Log-Likelihood:                -15007.
Date:                Mon, 24 Feb 2025   Deviance:                       22.808
Time:                        09:31:06   Pearson chi2:                     21.0
No. Iterations:                    16   Pseudo R-squ. (CS):             0.9999
Covariance Type:            nonrobust                                         
===========================================================================================================================
                                                              coef    std err          z      P>|z|      [0.025      0.975]
---------------------------------------------------------------------------------------------------------------------------
Intercept                                                3.538e+04   9146.181      3.868      0.000    1.75e+04    5.33e+04
C(LotConfig_agg)[T.Cul-de-sac]                           7371.5705   3190.969      2.310      0.021    1117.387    1.36e+04
C(LotConfig_agg)[T.Frontage on 2 / 3 sides of property] -7279.7501   3283.348     -2.217      0.027   -1.37e+04    -844.506
C(LotConfig_agg)[T.Inside lot]                           -769.4838   1468.900     -0.524      0.600   -3648.475    2109.507
C(GarageQual_agg)[T.Good]                                2.392e+04   6600.378      3.624      0.000     1.1e+04    3.69e+04
C(GarageQual_agg)[T.No garage]                           6301.5373   2975.681      2.118      0.034     469.310    1.21e+04
C(GarageQual_agg)[T.Typical/Average]                     8050.4887   2476.034      3.251      0.001    3197.552    1.29e+04
C(Fireplaces_optb)[T.[0.50, 1.50)]                       5229.2710   1370.680      3.815      0.000    2542.787    7915.755
C(Fireplaces_optb)[T.[1.50, inf)]                        1.039e+04   2916.039      3.564      0.000    4676.500    1.61e+04
C(KitchenQual)[T.Fair]                                  -3.067e+04   5209.495     -5.887      0.000   -4.09e+04   -2.05e+04
C(KitchenQual)[T.Good]                                  -2.384e+04   4401.467     -5.416      0.000   -3.25e+04   -1.52e+04
C(KitchenQual)[T.Typical/Average]                       -3.185e+04   4472.632     -7.121      0.000   -4.06e+04   -2.31e+04
C(BsmtQual)[T.Fair (70-79 inches)]                      -3.305e+04   5479.829     -6.032      0.000   -4.38e+04   -2.23e+04
C(BsmtQual)[T.Good (90-99 inches)]                      -3.039e+04   4484.103     -6.777      0.000   -3.92e+04   -2.16e+04
C(BsmtQual)[T.No basement]                               -1.87e+04   6215.754     -3.009      0.003   -3.09e+04   -6518.209
C(BsmtQual)[T.Typical (80-89 inches)]                   -3.237e+04   4766.224     -6.792      0.000   -4.17e+04    -2.3e+04
C(ExterQual)[T.Excellent]                                4.175e+04   8105.346      5.151      0.000    2.59e+04    5.76e+04
C(ExterQual)[T.Fair]                                    -3765.5427   3537.621     -1.064      0.287   -1.07e+04    3168.067
C(ExterQual)[T.Good]                                     6646.9038   2146.820      3.096      0.002    2439.215    1.09e+04
C(Exterior1st_agg)[T.Cement Board]                      -1.041e+04   4471.471     -2.329      0.020   -1.92e+04   -1649.054
C(Exterior1st_agg)[T.Metal Siding]                      -6823.8172   3454.438     -1.975      0.048   -1.36e+04     -53.243
C(Exterior1st_agg)[T.Other Exterior Materials]          -6443.0475   3886.565     -1.658      0.097   -1.41

## Analyses des performances

### Calculs des prédictions


In [61]:
df_test["SalePrice_pred"] = best_model.predict(df_test[selection])

### Quelques métriques bien connues


In [62]:
plot_perf(df_test["SalePrice"], df_test["SalePrice_pred"])

MAE          RMSE           MEE             ME        R2
0  17240.214235  29781.576613  11116.783386  252987.664383  0.879186

### Analyses des résidus


In [63]:
df_test["residus"] = df_test["SalePrice"] - df_test["SalePrice_pred"]

In [64]:
residuals_density(df_test, "residus")

In [ ]:
scat_res_price(
    df_test,
    "residus",
    "SalePrice",
)

In [ ]:
scat(
    df_test,
    "LotFrontage",
    "residus",
    numerical_cols,
)

In [ ]:
violin(
    df_test,
    "MSSubClass",
    "residus",
    categorical_cols,
)

D'autres méthodes pourraient apporter des résultats meilleurs. Déjà, la sélection des variables s'est faite avec les connaissances et les intuitions que j'avais, mais il est tout à fait possible de reprendre ce travail de manière plus classique, en passant par des principes de régressions pénalisées (Ridge, LASSO, ElasticNet). Une autre idée serait de passer à un lien logarithmique, mais je trouve l'interprétation des coefficients beaucoup moins évidente (c'est très personnel).

Globalement, avec la CV, les résultats sont un peu meilleurs. Mais les maisons chères sont trop peu nombreuses et le modèle n'est pas très bon dans ces zones-là. Il est possible d'anticiper avec la taille de l'étage : si l'étage est grand, il vaut mieux se déplacer pour estimer la maison.

Une autre idée consiste à passer à la méthode stacking.
